# Goal:
- Pull NASA LANCE Ultra Real Time (URT) Data via API call
- Preprocess and clean data
- Display fire perimeter on a map

API Resource Page: https://firms.modaps.eosdis.nasa.gov/api/area/html

Notes:
- Fire & Thermal Hotspots with REST API
- not the most consistent data pulls
- Sometimes a lot of data is shown, other times states "Error in processing: No data"
- requires email for a 'Map Key'
- 5000 credits, refreshes every 10 mins

In [1]:
import folium
from folium import plugins
import requests
import pandas as pd
from io import StringIO

global_url = "https://firms.modaps.eosdis.nasa.gov/api/area/csv/a17758d8f727c27ac9659247ed9ba826/VIIRS_NOAA21_NRT/world/5/2026-02-25"
usa_url = "https://firms.modaps.eosdis.nasa.gov/api/area/csv/a17758d8f727c27ac9659247ed9ba826/VIIRS_NOAA21_NRT/-124.7,24.5,-66.9,49.4/5/2026-02-25"
# returns in CSV format
response = requests.get(global_url)
print(f"Status Code: {response.status_code}")

Status Code: 200


In [2]:
# format CSV into StringIO object
csv_text = response.text.strip()
csv_file_object = StringIO(csv_text)

In [3]:
df = pd.read_csv(csv_file_object, sep=',')

In [4]:
df

latitude  longitude  bright_ti4  scan  track    acq_date  acq_time  \
0     -2.13033   17.79138      297.72  0.48   0.40  2026-02-25         0   
1     -1.86364   15.80856      302.76  0.42   0.45  2026-02-25         0   
2     -1.52924   29.25418      295.85  0.62   0.54  2026-02-25         0   
3     -1.52567   29.26401      311.62  0.63   0.54  2026-02-25         0   
4     -1.52423   29.25417      302.76  0.62   0.54  2026-02-25         0   
...        ...        ...         ...   ...    ...         ...       ...   
1937   5.52559   -3.66083      304.70  0.40   0.37  2026-02-25       141   
1938   6.31882  -10.67359      321.76  0.33   0.55  2026-02-25       141   
1939   6.39415   -9.12740      309.06  0.52   0.50  2026-02-25       141   
1940   6.47896   -5.02051      317.76  0.45   0.39  2026-02-25       141   
1941   6.47905   -5.02378      307.76  0.45   0.39  2026-02-25       141   

     satellite instrument confidence version  bright_ti5   frp daynight  
0          N21      VIIRS          n  2.0NRT      276.67  1.33        N  
1          N21      VIIRS          n  2.0NRT      286.21  1.60        N  
2          N21      VIIRS          n  2.0NRT      270.33  1.72        N  
3          N21      VIIRS          n  2.0NRT      271.66  1.72        N  
4          N21      VIIRS          n  2.0NRT      270.82  1.72        N  
...        ...        ...        ...     ...         ...   ...      ...  
1937       N21      VIIRS          n  2.0NRT      292.75  1.18        N  
1938       N21      VIIRS          n  2.0NRT      291.61  1.71        N  
1939       N21      VIIRS          n  2.0NRT      286.98  1.71        N  
1940       N21      VIIRS          n  2.0NRT      293.33  2.22        N  
1941       N21      VIIRS          n  2.0NRT      293.04  2.52        N  

[1942 rows x 14 columns]

In [5]:
# separate data into two dataframes
df_coords = df.loc[:, ("latitude", "longitude")]
df_metadata = df[["acq_date", "acq_time", "satellite", "instrument"]]

In [6]:
# initialize the map
m = folium.Map([40.0, -96.0], zoom_start=4, tiles="Cartodb dark_matter")

# layer for satellite hotspots
fire_hotspot_layer = folium.FeatureGroup(name='fire_hotspot_layer').add_to(m)

In [7]:
# create a list of dictionaries for the metadata
metadata_list = df_metadata.to_dict('records')

# zip the coordinates and metadata together for the loop
for coord, meta in zip(df_coords.values, metadata_list):
    x, y = coord[0], coord[1]
    
    # Create a nice string for the popup
    # Use <br> for line breaks in HTML
    html_popup = f"""
    <b>Satellite:</b> {meta['satellite']}<br>
    <b>Instrument:</b> {meta['instrument']}<br>
    <b>Date:</b> {meta['acq_date']}<br>
    <b>Time:</b> {meta['acq_time']}
    """
    
    folium.Marker(
        location=[x, y],
        # Tooltip shows on hover, Popup shows on click
        popup=folium.Popup(html_popup, max_width=200),
        tooltip="Click for Metadata",
        icon=folium.Icon(color="red", icon="fire", prefix="fa"),
    ).add_to(fire_hotspot_layer)

In [8]:
m